In [1]:
import pandas as pd

In [2]:
df = pd.read_excel("hoanmy_detect_task.xlsx")

In [3]:
df.head()

Location                                                Job  \
0  Khu vực Ngoại cảnh  Quét lá rụng, thu gom rác lối đi lại, lối xe c...   
1  Khu vực Ngoại cảnh  Nhặt rác bồn hoa cây cảnh, làm sạch gạch ốp xu...   
2  Khu vực Ngoại cảnh                         Vệ sinh gạt tàn, thùng rác   
3  Khu vực Ngoại cảnh  Lau các biển quảng cáo, biển chỉ dẫn (dưới 4m)...   
4  Khu vực Ngoại cảnh   Lau tường đá và kính bên ngoài tòa nhà (dưới 4m)   

  label  Name  luuluong  Dientichngoai  Dientichtrong  
0     1  BIDV         3           1144          11200  
1     1  BIDV         3           1144          11200  
2     1  BIDV         3           1144          11200  
3     1  BIDV         3           1144          11200  
4     2  BIDV         3           1144          11200

In [4]:
import pandas as pd
from pyvi import ViTokenizer


In [5]:
import pandas as pd
import re
import unicodedata

def normalize_text_keep_words(s: str) -> str:
    """
    Chuẩn hoá Unicode (NFC), lowercase, loại ký tự không phải chữ/số/khoảng trắng.
    Giữ toàn bộ từ vựng (CHƯA lọc stopword).
    """
    s = str(s)
    s = unicodedata.normalize('NFC', s).lower()
    s = re.sub(r"[^0-9a-zà-ỹ\s]", " ", s)
    s = re.sub(r"\s+", " ", s).strip()
    return s

def preprocess_step1_no_stopwords(df_raw: pd.DataFrame) -> pd.DataFrame:
    """
    df_raw: DataFrame gốc có cột 'Location', 'Job', 'label'
    Trả về df_out với các cột:
      - Location, Job, label (đã lọc 1-4)
      - location_clean, job_clean
      - combined_text = f"{location_clean} {job_clean}"
    """
    # 1) Bỏ nhãn rỗng và chỉ giữ {1,2,3,4}
    df = df_raw.dropna(subset=["label"]).copy()
    df["label"] = df["label"].astype(str).str.strip()
    df = df[df["label"].isin(["1","2","3","4"])].copy()

    # 2) Bổ sung thiếu Location, chuẩn kiểu
    df["Location"] = df["Location"].fillna("Unknown").astype(str)
    df["Job"] = df["Job"].astype(str)

    # 3) Làm sạch (CHƯA lọc stopword)
    df["location_clean"] = df["Location"].apply(normalize_text_keep_words)
    df["job_clean"]      = df["Job"].apply(normalize_text_keep_words)

    # 4) Ghép Location + Job (location trước, job sau)
    df["combined_text"] = (df["location_clean"] + " " + df["job_clean"]).str.strip()

    # 5) Trả về gọn gàng
    return df


In [6]:
df_out = preprocess_step1_no_stopwords(df)


In [7]:
import pandas as pd
from pyvi import ViTokenizer

# === 1. Đọc stopword từ file txt ===
def load_stopwords(path):
    """
    Đọc file stopword (.txt), mỗi dòng là 1 từ/cụm từ, loại bỏ dòng trống.
    """
    with open(path, "r", encoding="utf-8") as f:
        stopwords = [line.strip() for line in f if line.strip()]
    return set(stopwords)

stopwords_path = "vietnamese-stopwords-dash.txt"  # đường dẫn file stopword của bạn
vietnamese_stopwords = load_stopwords(stopwords_path)

# === 2. Hàm tách từ và loại stopword ===
def segment_and_remove_stopwords(text):
    """
    Tách từ bằng PyVi -> loại stopword theo danh sách.
    """
    if not isinstance(text, str):
        return ""
    segmented = ViTokenizer.tokenize(text)
    tokens = segmented.split()
    filtered = [tok for tok in tokens if tok not in vietnamese_stopwords]
    return " ".join(filtered)

# === 3. Áp dụng cho dữ liệu đã tiền xử lý (df_out từ bước 1) ===
# df_out = preprocess_step1_no_stopwords(df_raw)  # từ bước 1
df_out["tokenized_text"] = df_out["combined_text"].apply(segment_and_remove_stopwords)

# === 4. Xem thử vài dòng kết quả ===
df_out[["combined_text", "tokenized_text"]].head(10)


combined_text  \
0  khu vực ngoại cảnh quét lá rụng thu gom rác lố...   
1  khu vực ngoại cảnh nhặt rác bồn hoa cây cảnh l...   
2       khu vực ngoại cảnh vệ sinh gạt tàn thùng rác   
3  khu vực ngoại cảnh lau các biển quảng cáo biển...   
4  khu vực ngoại cảnh lau tường đá và kính bên ng...   
5         khu vực ngoại cảnh vệ sinh họng rác nếu có   
6  khu vực ngoại cảnh phun rửa sân bằng máy phun ...   
7  khu vực ngoại cảnh khu vực tập kết rác thải củ...   
8  khu vực ngoại cảnh làm sạch các chòi bảo vệ và...   
9  khu vực ngoại cảnh lau kính mặt dưới mái kính ...   

                                      tokenized_text  
0  khu_vực ngoại_cảnh quét lá rụng thu_gom rác lố...  
1  khu_vực ngoại_cảnh nhặt rác bồn hoa cây_cảnh s...  
2       khu_vực ngoại_cảnh_vệ_sinh gạt_tàn thùng rác  
3  khu_vực ngoại_cảnh lau biển quảng_cáo biển chỉ...  
4        khu_vực ngoại_cảnh lau tường đá kính tòa 4m  
5                khu_vực ngoại_cảnh_vệ_sinh họng rác  
6    khu_vực ngoại_cảnh phun rửa sân máy phun áp_lực  
7    khu_vực ngoại_cảnh khu_vực tập_kết rác_thải tòa  
8  khu_vực ngoại_cảnh sạch chòi bảo_vệ thùng rác ...  
9  khu_vực ngoại_cảnh lau kính mặt mái kính sảnh ...

In [8]:
def remove_token_khu_vuc(text):
    if not isinstance(text, str):
        return ""
    tokens = text.split()
    tokens = [t for t in tokens if t != "khu_vực"]
    return " ".join(tokens)

df_out["tokenized_text"] = df_out["tokenized_text"].apply(remove_token_khu_vuc)


In [72]:
df_out.columns

Index(['Location', 'Job', 'label', 'Name', 'luuluong', 'Dientichngoai',
       'Dientichtrong', 'location_clean', 'job_clean', 'combined_text',
       'tokenized_text'],
      dtype='object')

In [31]:
# Giữ lại chỉ label 1, 2, 3
df_out = df_out[df_out["label"].astype(str).isin(["1", "2", "3"])].reset_index(drop=True)

print("Số dòng sau khi giữ label 1-3:", df_out.shape)
print(df_out["label"].value_counts())


Số dòng sau khi giữ label 1-3: (769, 11)
label
1    440
2    223
3    106
Name: count, dtype: int64


In [122]:
# ==== BƯỚC 1: chỉ giữ label 1–3 (nếu cần) ====
df_out = df_out[df_out["label"].astype(str).isin(["1", "2", "3"])].reset_index(drop=True)

# ==== BƯỚC 2: định nghĩa 2 tập test + 1 tập hold-out ====
test_buildings = ["Keangnam", "CMC"]          # tập test chính
holdout_building = ["HH4"]                  # ví dụ: tập kiểm thử ngoài (bạn đổi tên tòa tùy ý)

# ==== BƯỚC 3: Tách dữ liệu ====

# Tập test theo 2 tòa chính
test_df = df_out[df_out["Name"].isin(test_buildings)].reset_index(drop=True)

# Tập hold-out theo tòa riêng
holdout_df = df_out[df_out["Name"].isin(holdout_building)].reset_index(drop=True)

# Tập train: tất cả còn lại
train_df = df_out[
    ~df_out["Name"].isin(test_buildings + holdout_building)
].reset_index(drop=True)

print("Train:", train_df.shape)
print("Test :", test_df.shape)
print("Hold-out:", holdout_df.shape)

print("\nSố lượng theo từng tập:")
print("Train buildings:", train_df["Name"].unique())
print("Test  buildings:", test_df["Name"].unique())
print("Hold-out building:", holdout_df["Name"].unique())


Train: (536, 11)
Test : (172, 11)
Hold-out: (61, 11)

Số lượng theo từng tập:
Train buildings: ['BIDV' 'CenterPoint ' 'HCO' 'Hong Kong' 'Sunred' '138A Giang Vo'
 'VIGALCERA']
Test  buildings: ['CMC' 'Keangnam']
Hold-out building: ['HH4']


In [123]:
def location_similarity(q_row, cand_row):
    """
    Độ tương đồng Location trong [0,1] – càng cao càng giống.
    Dùng Jaccard trên token của location_clean.
    """
    q_tokens = set(str(q_row["location_clean"]).split())
    c_tokens = set(str(cand_row["location_clean"]).split())

    if not q_tokens or not c_tokens:
        return 0.0

    inter = len(q_tokens & c_tokens)
    union = len(q_tokens | c_tokens)
    return inter / union


In [124]:
from transformers import AutoTokenizer, AutoModel
import torch

device = "cuda" if torch.cuda.is_available() else "cpu"

tokenizer = AutoTokenizer.from_pretrained("dangvantuan/vietnamese-embedding")
model = AutoModel.from_pretrained("dangvantuan/vietnamese-embedding").to(device)


In [125]:
def embed_text(text, tokenizer, model, device=device):
    # Tokenize
    encoded = tokenizer(
        text,
        padding=True,
        truncation=True,
        max_length=128,
        return_tensors="pt"
    ).to(device)

    with torch.no_grad():
        output = model(**encoded)

    # output.last_hidden_state: [batch, seq_len, hidden]
    token_embeddings = output.last_hidden_state          # (1, L, H)
    attention_mask = encoded["attention_mask"]           # (1, L)

    # Mean pooling
    mask = attention_mask.unsqueeze(-1).expand(token_embeddings.size()).float()
    sum_embeds = (token_embeddings * mask).sum(dim=1)
    lengths = mask.sum(dim=1)
    mean_pooled = sum_embeds / lengths

    return mean_pooled.cpu()    # return vector (1, hidden)


In [126]:
train_texts = train_df["tokenized_text"].tolist()

train_embeddings = []
for txt in train_texts:
    vec = embed_text(txt, tokenizer, model)
    train_embeddings.append(vec.squeeze(0))

train_embeddings = torch.stack(train_embeddings)   # shape: (N, hidden)


In [127]:
def cosine_sim(a, b):
    a = a / a.norm(dim=-1, keepdim=True)
    b = b / b.norm(dim=-1, keepdim=True)
    return torch.mm(a, b.t())   # (1,H) x (H,N) = (1,N)


In [128]:
import numpy as np

def numeric_closeness(q_row, cand_row, alpha_out=0.7, alpha_in=0.7):

    # closeness lưu lượng
    if q_row["luuluong"] == cand_row["luuluong"]:
        c_luu = 1.0
    elif abs(q_row["luuluong"] - cand_row["luuluong"]) == 1:
        c_luu = 0.6
    else:
        c_luu = 0.3

    # closeness diện tích
    d_out = abs(np.log1p(q_row["Dientichngoai"]) - np.log1p(cand_row["Dientichngoai"]))
    d_in  = abs(np.log1p(q_row["Dientichtrong"])  - np.log1p(cand_row["Dientichtrong"]))

    c_out = np.exp(-alpha_out * d_out)
    c_in  = np.exp(-alpha_in  * d_in)

    return 0.5 * c_luu + 0.25 * c_out + 0.25 * c_in


In [129]:
def predict_label_for_row(q_row, train_df, train_embeddings,
                          tokenizer, model,
                          top_k=10, w_numeric=0.4, w_loc=0.6):
    """
    Bước 1: dùng embedding để chọn top_k ứng viên gần nghĩa nhất (theo tokenized_text).
    Bước 2: trong top_k đó, KHÔNG dùng điểm text nữa, chỉ dùng:
        - loc_sim   : similarity theo location_clean  [0,1]  (quan trọng nhất)
        - num_c     : numeric_closeness (luuluong + diện tích)  (~0..1.5)
    final_score = w_loc * loc_sim + w_numeric * num_c
    """

    # 1) embed query
    q_vec = embed_text(q_row["tokenized_text"], tokenizer, model)  # (1, H)

    # 2) cosine similarity với toàn bộ train → chỉ để CHỌN ỨNG VIÊN
    sims = cosine_sim(q_vec, train_embeddings)[0]  # (N,)

    # 3) lấy top-k job gần nhất theo embedding
    top_k = min(top_k, len(train_df))
    top_scores, top_idx = torch.topk(sims, k=top_k)

    label_scores = {}

    for score, idx in zip(top_scores, top_idx):
        cand_row = train_df.iloc[int(idx)]

        # location similarity (quan trọng nhất)
        loc_sim = location_similarity(q_row, cand_row)

        # numeric closeness (luuluong + diện tích)
        num_c = numeric_closeness(q_row, cand_row)

        # điểm cuối cho neighbor này
        final_score = w_loc * loc_sim + w_numeric * num_c

        lbl = str(cand_row["label"])
        label_scores[lbl] = label_scores.get(lbl, 0.0) + final_score

    # fallback nếu không có ứng viên
    if not label_scores:
        majority_label = str(train_df["label"].value_counts().idxmax())
        return majority_label, {}

    best_label = max(label_scores, key=label_scores.get)
    return best_label, label_scores


In [132]:
preds = []
scores_debug = []

for _, row in test_df.iterrows():
    pred, sc = predict_label_for_row(
        row,
        train_df,
        train_embeddings,
        tokenizer,
        model,
        top_k=5,
        w_numeric=0.3,
        w_loc=0.7
    )
    preds.append(pred)
    scores_debug.append(sc)

test_df["pred_label_hf"] = preds
test_df["score_details"] = scores_debug


In [133]:
from sklearn.metrics import classification_report

print(classification_report(
    test_df["label"].astype(str),
    test_df["pred_label_hf"].astype(str),
    digits=3
))


              precision    recall  f1-score   support

           1      0.804     0.857     0.829       105
           2      0.600     0.447     0.512        47
           3      0.400     0.500     0.444        20

    accuracy                          0.703       172
   macro avg      0.601     0.601     0.595       172
weighted avg      0.701     0.703     0.698       172



In [92]:
# Lọc các trường hợp dự đoán sai
mis_df = test_df[
    test_df["label"].astype(str) != test_df["pred_label_hf"].astype(str)
].copy()

print("Số mẫu dự đoán sai:", len(mis_df))

# Xem 10 dòng đầu cho gọn
cols_show = [
    "label", "pred_label_hf",
    "Name", "Location",
    "luuluong", "Dientichngoai", "Dientichtrong",
    "Job", "tokenized_text"
]

print(mis_df[cols_show].head(10).to_string(index=False))


Số mẫu dự đoán sai: 53
label pred_label_hf Name                                                                    Location  luuluong  Dientichngoai  Dientichtrong                                                      Job                                                                  tokenized_text
    3             1  CMC                                       Khu vực ngoại cảnh, vỉa hè xung quanh         1            900           5235 Lau sạch các biển báo, biển tên công ty (độ cao dưới 4m)               ngoại_cảnh vỉa_hè xung_quanh lau sạch biển_báo biển công_ty độ 4m
    3             1  CMC                                       Khu vực ngoại cảnh, vỉa hè xung quanh         1            900           5235                               Vệ sinh lối ra vào, vỉa hè                                 ngoại_cảnh vỉa_hè xung_quanh vệ_sinh lối vỉa_hè
    3             2  CMC                                       Khu vực ngoại cảnh, vỉa hè xung quanh         1            900           5235   

In [93]:
max_cases = 10  # đổi số nếu muốn xem nhiều hơn

for i, (_, row) in enumerate(mis_df.iterrows(), start=1):
    if i > max_cases:
        break

    print("\n" + "="*80)
    print(f"❌ CASE #{i}")
    print(f"  True label    : {row['label']}")
    print(f"  Pred label    : {row['pred_label_hf']}")
    print(f"  Tòa           : {row['Name']}")
    print(f"  Location      : {row['Location']}")
    print(f"  Lưu lượng     : {row['luuluong']}")
    print(f"  DT ngoài      : {row['Dientichngoai']}")
    print(f"  DT trong      : {row['Dientichtrong']}")
    print("  Job raw       :", row['Job'])
    print("  tokenized_text:", row['tokenized_text'])



❌ CASE #1
  True label    : 3
  Pred label    : 1
  Tòa           : CMC
  Location      : Khu vực ngoại cảnh, vỉa hè xung quanh
  Lưu lượng     : 1
  DT ngoài      : 900
  DT trong      : 5235
  Job raw       : Lau sạch các biển báo, biển tên công ty (độ cao dưới 4m)
  tokenized_text: ngoại_cảnh vỉa_hè xung_quanh lau sạch biển_báo biển công_ty độ 4m

❌ CASE #2
  True label    : 3
  Pred label    : 1
  Tòa           : CMC
  Location      : Khu vực ngoại cảnh, vỉa hè xung quanh
  Lưu lượng     : 1
  DT ngoài      : 900
  DT trong      : 5235
  Job raw       : Vệ sinh lối ra vào, vỉa hè
  tokenized_text: ngoại_cảnh vỉa_hè xung_quanh vệ_sinh lối vỉa_hè

❌ CASE #3
  True label    : 3
  Pred label    : 2
  Tòa           : CMC
  Location      : Khu vực ngoại cảnh, vỉa hè xung quanh
  Lưu lượng     : 1
  DT ngoài      : 900
  DT trong      : 5235
  Job raw       : Vệ sinh rãnh thoát nước
  tokenized_text: ngoại_cảnh vỉa_hè xung_quanh vệ_sinh rãnh thoát

❌ CASE #4
  True label    : 2
  Pred la

In [61]:
import pandas as pd
import torch

mis_df = test_df[
    test_df["label"].astype(str) != test_df["pred_label_hf"].astype(str)
].copy()

print("Số mẫu dự đoán sai:", len(mis_df))


Số mẫu dự đoán sai: 54


In [100]:
def get_top_neighbors(q_row,
                      train_df,
                      train_embeddings,
                      tokenizer,
                      model,
                      top_k=10,
                      w_numeric=0.3,
                      w_loc=0.6):
    q_vec = embed_text(q_row["tokenized_text"], tokenizer, model)
    sims = cosine_sim(q_vec, train_embeddings)[0]

    top_k = min(top_k, len(train_df))
    top_scores, top_idx = torch.topk(sims, k=top_k)

    w_text = 1.0 - w_numeric - w_loc

    rows = []
    for score, idx in zip(top_scores, top_idx):
        score = float(score.item())
        cand = train_df.iloc[int(idx)].copy()

        num_c   = numeric_closeness(q_row, cand)
        loc_sim = location_similarity(q_row, cand)

        final_score = (
            w_loc    * loc_sim +
            w_numeric * num_c +
            w_text   * score
        )

        cand["cos_sim"]       = score
        cand["loc_sim"]       = loc_sim
        cand["num_closeness"] = num_c
        cand["final_score"]   = final_score
        rows.append(cand)

    neighbors_df = pd.DataFrame(rows).sort_values("final_score", ascending=False)
    return neighbors_df


In [95]:
max_cases = 54  # đổi nếu muốn xem nhiều hơn

for i, (_, row) in enumerate(mis_df.iterrows(), start=1):
    if i > max_cases:
        break
    if i!=50:
       continue     
    print("\n" + "="*100)
    print(f"❌ CASE SAI #{i}")
    print(f"  True label      : {row['label']}")
    print(f"  Pred label      : {row['pred_label_hf']}")
    print(f"  Tòa (Name)      : {row['Name']}")
    print(f"  Location        : {row['Location']}")
    print(f"  Lưu lượng       : {row['luuluong']}")
    print(f"  DT ngoài (m2)   : {row['Dientichngoai']}")
    print(f"  DT trong (m2)   : {row['Dientichtrong']}")
    print("  Job raw         :", row["Job"])
    print("  tokenized_text  :", row["tokenized_text"])

    # Lấy neighbors
    neighbors = get_top_neighbors(
        row,
        train_df,
        train_embeddings,
        tokenizer,
        model,
        top_k=10,
        w_numeric=0.7   # giữ giống lúc bạn train để dễ so
    )

    print("\n  → Top 10 job tương đồng trong train:")
    cols_show = [
        "label", "Name", "Location",
        "luuluong", "Dientichngoai", "Dientichtrong",
        "Job", "tokenized_text",
        "cos_sim", "num_closeness", "final_score"
    ]
    print(neighbors[cols_show].to_string(index=False))



❌ CASE SAI #50
  True label      : 3
  Pred label      : 2
  Tòa (Name)      : Keangnam
  Location        : KHU VỰC THANG BỘ (02 thang/ tháp)
  Lưu lượng       : 2
  DT ngoài (m2)   : 46056
  DT trong (m2)   : 609673
  Job raw         : · Lau quạt thông gió
  tokenized_text  : thang 02 thang tháp lau quạt thông_gió

  → Top 10 job tương đồng trong train:
label         Name                           Location  luuluong  Dientichngoai  Dientichtrong                                                         Job                                         tokenized_text  cos_sim  num_closeness  final_score
    2    Hong Kong        KHU VỰC THANG BỘ (4 thang )         2           9950          25630                                          · Lau lỗ thông gió                         thang 4 thang lau lỗ thông_gió 0.729290       0.612730     0.437822
    1         BIDV     Khu vực thang bộ (02 thang bộ)         3           1144          11200            Làm sạch mặt ngoài cửa thông gió, biển hiệu t

DỰ ĐOÁN TẬP HOLD OUT

In [ ]:
holdout_preds = []
holdout_scores_debug = []

for _, row in holdout_df.iterrows():
    pred, sc = predict_label_for_row(
        row,
        train_df,
        train_embeddings,
        tokenizer,
        model,
        top_k=10,          # số ứng viên lấy theo ST
        w_numeric=0.3,     # bạn có thể tune
        w_loc=0.7          # location quan trọng nhất
    )
    holdout_preds.append(pred)
    holdout_scores_debug.append(sc)

holdout_df["pred_label_hf"] = holdout_preds
holdout_df["score_details"] = holdout_scores_debug
